# Datensatz: Namentliche Abstimmungen im Bundestag

(Die Idee für diese Analyse kommt von Prof. Frank Vallentin, Mathematisches Institut, UzK).

Die Rohdaten sind auf [dieser Seite des deutschen Bundestages](https://www.bundestag.de/parlament/plenum/abstimmung/liste) verlinkt.
Es ist eine etwas übertriebene JavaScript-Konstruktion, daher nicht direkt mit einfachen Tools maschinenlesbar.
Ich habe die Seite daher in Chrome aufgerufen und als "liste.html" gespeichert.

Mit folgenden Skript habe ich dann die Tabellen mit den Abstimmungsergebnissen heruntergeladen:

    grep -o "https://www.bundestag.de/resource/blob/.*xlsx" liste.html >urls
    for url in `cat urls`; do
    	wget $url
    done

Das Ergebnis sind 30 Excel-Dateien, eine pro Abstimmung.

Der Code unten liest die Dateien und speichert die Abstimmungsergebnisse in leicht lesbaren CSV-Dateien ab.

In [2]:
import pandas as pd
import numpy as np
import glob as glob
import csv

In [3]:
def bundestagToPandaFrame(f):
    xl_file = pd.ExcelFile(f) 
    
    # dictionary with one entry per sheet
    dfs = {sheet_name: xl_file.parse(sheet_name) 
              for sheet_name in xl_file.sheet_names}
    
    # in our case, files contain only one sheet
    # it is represented as a pandas dataframe
    return(list(dfs.values())[0])

# collect all excel files
files = glob.glob('./20*xlsx')

In [5]:
# create a dictionary of MdBs from first file

df = bundestagToPandaFrame(files[0])

voteDict = {}
frakDict = {}

for idx, row in df.iterrows():
    voteDict[row['Bezeichnung']] = []
    frakDict[row['Bezeichnung']] = row['Fraktion/Gruppe']

In [12]:
for file in files:
    df = bundestagToPandaFrame(file)

    for idx, row in df.iterrows():
        vote = 0
        if row['ja']==1:
            vote = 1
        elif row['nein']==1:
            vote = -1

        bez = row['Bezeichnung']
        
        if bez in voteDict:
            voteDict[bez] += [vote]

with open('files.lst', 'w', newline='') as csvfile:
    writer = csv.writer(csvfile, delimiter='\n', quotechar='|', quoting=csv.QUOTE_MINIMAL)
    writer.writerow(files)

In [7]:
names = []
fraktionen = []
votes = []

for bez in voteDict:
    # Keep only those MdBs who are accounted for in every file
    if len(voteDict[bez]) == len(files):
        names += [bez]
        votes += [voteDict[bez]]
        fraktionen += [frakDict[bez]]

with open('votes.csv', 'w', newline='') as csvfile:
    writer = csv.writer(csvfile, delimiter=' ', quotechar='|', quoting=csv.QUOTE_MINIMAL)
    for vote in votes:
        writer.writerow(vote)
        
with open('names.lst', 'w', newline='') as csvfile:
    writer = csv.writer(csvfile, delimiter='\n', quotechar='|', quoting=csv.QUOTE_MINIMAL)
    writer.writerow(names)
        
with open('fraks.lst', 'w', newline='') as csvfile:
    writer = csv.writer(csvfile, delimiter='\n', quotechar='|', quoting=csv.QUOTE_MINIMAL)
    writer.writerow(fraktionen)